data reading from source



In [0]:
df=spark.sql("select * from databricks_cata.silver.acute_discharge_situation")

In [0]:
from pyspark.sql.functions import col, count

# 1. List all columns
all_cols = df.columns

# 2. Group by every column, count duplicates
dups = (
    df.groupBy(all_cols)
      .agg(count("*").alias("cnt"))
      .filter(col("cnt") > 1)
)

# 3. Show you any truly identical rows
dups.show(truncate=False)


In [0]:
dups.count()

In [0]:
from pyspark.sql import functions as F

# 1. Compute true min/max dates as before
min_max = (
    df
    .withColumn("period_date", F.to_date("period", "yyyy-MM-dd"))
    .agg(
        F.min("period_date").alias("start_date"),
        F.max("period_date").alias("end_date")
    )
    .collect()[0]
)
start = min_max["start_date"]
end   = min_max["end_date"]

# 2. Generate one seed row, then sequence & explode
calendar_df = (
    spark.range(1)   # single row with id = 0
         .selectExpr(
             f"sequence(to_date('{start}'), to_date('{end}'), interval 1 day) AS dt"
         )
         .select(F.explode("dt").alias("date_key"))
         .withColumn("year",        F.year("date_key"))
         .withColumn("month",       F.month("date_key"))
         .withColumn("day",         F.dayofmonth("date_key"))
         .withColumn("day_of_week", F.dayofweek("date_key"))
         .withColumn("is_weekend",  F.expr("day_of_week IN (1,7)"))
)

display(calendar_df)  # you should now see one row per date


In [0]:
calendar_df.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.dim_date")

In [0]:
%sql
select * from databricks_cata.gold.dim_date

In [0]:
dim_region = (df
  .filter("level = 'Region'")
  .selectExpr("org_code as region_code", "org_name as region_name")
  .distinct()
)

dim_region.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.dim_region")


In [0]:
%sql
select * from databricks_cata.gold.dim_region

In [0]:
dim_icb = (df
  .filter("level = 'ICB'")
  .selectExpr("org_code as icb_code", "org_name as icb_name", "region as region_code")
  .distinct()
)

dim_icb.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.dim_icb")


In [0]:
%sql
select * from databricks_cata.gold.dim_icb

In [0]:
dim_metric = (df
  .select("metric_group","metric","metric_type")
  .distinct()
)

dim_metric.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.dim_metric")


In [0]:
%sql
select * from databricks_cata.gold.dim_metric

In [0]:
df_silver = df.withColumn("period_date", F.to_date("period", "yyyy-MM-dd"))

In [0]:
display(df_silver)

In [0]:
from pyspark.sql.functions import to_date

spark.table("databricks_cata.silver.acute_discharge_situation") \
  .filter("level = 'ICB'") \
  .selectExpr(
    "to_date(period,'yyyy-MM-dd') AS date_key",
    "org_code",
    "metric_group",
    "value",
    "year",
    "month"
  ) \
  .write \
  .mode("overwrite") \
  .partitionBy("year","month") \
  .format("delta") \
  .saveAsTable("databricks_cata.gold.fact_daily_sitrep")


In [0]:
%sql
select * from databricks_cata.gold.fact_daily_sitrep

In [0]:
from pyspark.sql.functions import expr, col

fact_wide = (
  spark.table("databricks_cata.gold.fact_daily_sitrep")
    .groupBy("date_key", "year", "month", "org_code")
    .pivot("metric_group")
    .agg(expr("sum(value)"))
)

# Rename columns to remove spaces
for col_name in fact_wide.columns:
    new_col_name = col_name.replace(" ", "_")
    fact_wide = fact_wide.withColumnRenamed(col_name, new_col_name)

fact_wide.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.vw_fact_wide")

In [0]:
%sql
select * from databricks_cata.gold.vw_fact_wide

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# 1a) Add year/month columns
fact_monthly = (
    spark.table("vw_fact_wide")
      .withColumn("year",   F.year("date_key"))
      .withColumn("month",  F.month("date_key"))
)

# 1b) Aggregate to month × ICB
monthly_agg = (
    fact_monthly
      .groupBy("org_code","year","month")
      .agg(
        F.sum(F.col("NCTR")).alias("total_delays"),       # NCTR = count of patients delayed
        F.sum(F.col("Discharges")).alias("total_discharges")   # DISCH = count of discharges (if available)
      )
      .withColumn(
        "delay_rate",
        # per-100 discharges; if DISCH is null/zero you’d need to handle separately
        F.when(
          F.col("total_discharges")>0,
          F.col("total_delays")/F.col("total_discharges")*100
        ).otherwise(None)
      )
)

monthly_agg.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.vw_monthly_rates")

In [0]:
%sql
select * from databricks_cata.gold.vw_monthly_rates order by  year asc, month asc

In [0]:
# 2a) Peer averages & stddev by month
peer_stats = (
    spark.table("databricks_cata.gold.vw_monthly_rates")
      .groupBy("year","month")
      .agg(
        F.mean("delay_rate").alias("peer_avg_rate"),
        F.stddev("delay_rate").alias("peer_stddev_rate")
      )
)

# 2b) Join back & compute Z-score
peer_benchmarked = (
    spark.table("databricks_cata.gold.vw_monthly_rates")
      .join(peer_stats, ["year","month"])
      .withColumn(
        "z_score",
        (F.col("delay_rate") - F.col("peer_avg_rate")) / F.col("peer_stddev_rate")
      )
)

peer_benchmarked.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.vw_peer_benchmarked")

In [0]:
%sql
select * from databricks_cata.gold.vw_peer_benchmarked order by year asc, month asc 

In [0]:
# 5a) Monthly sum of A8 per ICB
barrier_monthly = (
    fact_monthly
      .groupBy("org_code","year","month")
      .agg(F.sum("A8").alias("transport_delays"))
)

# 5b) Peer stats and z-score
barrier_peer = (
    barrier_monthly
      .join(
        barrier_monthly
          .groupBy("year","month")
          .agg(
            F.mean("transport_delays").alias("peer_avg"),
            F.stddev("transport_delays").alias("peer_std")
          ),
        ["year","month"]
      )
      .withColumn(
        "z_score_transport",
        (F.col("transport_delays") - F.col("peer_avg")) / F.col("peer_std")
      )
      .select("year","month","transport_delays","peer_avg","z_score_transport")
)
display(barrier_peer)


In [0]:
from pyspark.sql import functions as F

# 1) unpivot A1–A8 into barrier, count
barrier_unpivot = (
  spark.table("databricks_cata.gold.vw_fact_wide")
    .selectExpr(
      "date_key", "org_code as icb_code",
      "year", "month",
      """
      stack(
        8,
        'A1', A1,
        'A2', A2,
        'A3', A3,
        'A4', A4,
        'A5', A5,
        'A6', A6,
        'A7', A7,
        'A8', A8
      ) AS (barrier, delay_count)
      """
    )
    .filter("delay_count IS NOT NULL")
)

# 2) aggregate to month×ICB×barrier
barrier_monthly = (
  barrier_unpivot
    .groupBy("icb_code","year","month","barrier")
    .agg(F.sum("delay_count").alias("total_barrier"))
)

# 3) compute peer avg & stddev per barrier×month
peer_barrier_stats = (
  barrier_monthly
    .groupBy("barrier","year","month")
    .agg(
      F.mean("total_barrier").alias("peer_avg"),
      F.stddev("total_barrier").alias("peer_std")
    )
)

# 4) join back & z-score
barrier_zscores = (
  barrier_monthly
    .join(peer_barrier_stats, ["barrier","year","month"])
    .withColumn(
      "z_score_barrier",
      (F.col("total_barrier") - F.col("peer_avg")) / F.col("peer_std")
    )
)

barrier_zscores.createOrReplaceTempView("vw_barrier_zscores")


In [0]:
%sql
SELECT * 
FROM vw_barrier_zscores
ORDER BY year, month, barrier, icb_code


In [0]:
barrier_zscores.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.vw_barrier_zscores")

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# 1) Define exactly which metric_group columns you want to include
metrics = [
    "NCTR",
    "A1",
    "A2",
    "A3",
    "A4",
    "A5",
    "A6",
    "A7",
    "A8",
    "Additional_bed_days_lost"
]

# 2) Aggregate each metric by month × ICB, then unpivot with stack()
reason_monthly = (
    spark
      .table("databricks_cata.gold.vw_fact_wide")
      .groupBy("org_code", "year", "month")
      .agg(
        *[F.sum(F.col(m)).alias(m) for m in metrics]
      )
      .selectExpr(
        "org_code", "year", "month",
        f"""
        stack(
          {len(metrics)},
          {', '.join([f"'{m}', `{m}`" for m in metrics])}
        ) AS (reason, count)
        """
      )
      .filter("count IS NOT NULL")      # drop any null‐count rows
)

# 3) Rank each reason within its ICB × month by descending count
window_spec = Window.partitionBy("org_code", "year", "month") \
                    .orderBy(F.desc("count"))

top_reasons = (
    reason_monthly
      .withColumn("rank", F.rank().over(window_spec))
      .filter("rank <= 3")
)

top_reasons.write.mode("overwrite").format("delta").saveAsTable("databricks_cata.gold.vw_top_reasons")


In [0]:
%sql
select * from databricks_cata.gold.vw_top_reasons

In [0]:
%sql
SELECT org_code, year, month, reason, count
FROM vw_top3_reasons
ORDER BY org_code, year, month, rank;


In [0]:
%sql
Select * from databricks_cata.gold.dim_metric

In [0]:
%sql
select * from databricks_cata.gold.vw_barrier_zscores

In [0]:
%sql
select * from databricks_cata.gold.fact_daily_sitrep

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# 0) Start from your wide fact
fact = spark.table("databricks_cata.gold.vw_fact_wide")

# 1) Fill NULLs → 0 for A1–A8
for b in ["A1","A2","A3","A4","A5","A6","A7","A8"]:
    fact = fact.withColumn(b, F.coalesce(F.col(b), F.lit(0)))

# 2) Unpivot *including* zeros (no filter)
barrier_unpivot = fact.selectExpr(
    "org_code as icb_code", "year", "month",
    """
    stack(
      8,
      'A1', A1,
      'A2', A2,
      'A3', A3,
      'A4', A4,
      'A5', A5,
      'A6', A6,
      'A7', A7,
      'A8', A8
    ) AS (barrier, total_barrier)
    """
)

# 3) Compute peer stats & Z-score exactly as before
peer_barrier_stats = (
    barrier_unpivot
      .groupBy("barrier","year","month")
      .agg(
        F.mean("total_barrier").alias("peer_avg"),
        F.stddev("total_barrier").alias("peer_std")
      )
)

barrier_zscores = (
    barrier_unpivot
      .join(peer_barrier_stats, ["barrier","year","month"])
      .withColumn("z_score_barrier",
          (F.col("total_barrier") - F.col("peer_avg")) / F.col("peer_std")
      )
)

barrier_zscores.createOrReplaceTempView("vw_barrier_zscores")


In [0]:
%sql
select * from vw_barrier_zscores

In [0]:
barrier_zscores.write.format("delta").mode("overwrite").saveAsTable("databricks_cata.gold.vw_barrier_zscores")

In [0]:
%sql
select count(*) as ctr_count
from databricks_cata.gold.fact_daily_sitrep
where metric_group = 'CTR'

In [0]:
%sql
select * from databricks_cata.gold.fact_daily_sitrep where metric_group = "Discharge destination"

date_key org_code metric_group value year month 2025-03-01 QRL Discharge destination 421 2025 3 2025-03-01 QMJ Discharge destination 80 2025 3 2025-03-01 QUY Discharge destination 172 2025 3 2025-03-01 QT1 Discharge destination 56 2025 3 2025-03-01 QWU Discharge destination 170 2025 3 2025-03-01 QKK Discharge destination 199 2025 3 2025-03-01 QWO Discharge destination 166 2025 3 2025-03-01 QHM Discharge destination 304 2025 3 2025-03-01 QJM Discharge destination 43 2025 3 2025-03-01 QOP Discharge destination 157 2025 3 2025-03-01 QK1 Discharge destination 86 2025 3 2025-03-01 QM7 Discharge destination 80 2025 3 2025-03-01 QNX Discharge destination 285 2025 3 2025-03-01 QMF Discharge destination 248 2025 3 2025-03-01 QJM Discharge destination 114 2025 3 2025-03-01 QHL Discharge destination 2426 2025 3 2025-03-01 QYG Discharge destination 14 2025 3 2025-03-01 QYG Discharge destination 1068 2025 3 2025-03-01 QWO Discharge destination 13536 2025 3 2025-03-01 QK1 Discharge destination 34 2025 3 2025-03-01 QU9 Discharge destination 149 2025 3 2025-03-01 QMJ Discharge destination 498 2025 3 2025-03-01 QJG Discharge destination 6068 2025 3 2025-03-01 QVV Discharge destination 1 2025 3 2025-03-01 QVV Discharge destination 31 2025 3 2025-03-01 QGH Discharge destination 70 2025 3 2025-03-01 QJK Discharge destination 48 2025 3 2025-03-01 QR1 Discharge destination 128 2025 3 2025-03-01 QMF Discharge destination 163 2025 3 2025-03-01 QKS Discharge destination 144 2025 3 2025-03-01 QOX Discharge destination 645 2025 3 2025-03-01 QWU Discharge destination 489 2025 3 2025-03-01 QE1 Discharge destination 8235 2025 3 2025-03-01 QPM Discharge destination 2956 2025 3 2025-03-01 QNX Discharge destination 30 2025 3 2025-03-01 QSL Discharge destination 2832 2025 3 2025-03-01 QKK Discharge destination 6 2025 3 2025-03-01 QOX Discharge destination 161 2025 3 2025-03-01 QJG Discharge destination 1 2025 3 2025-03-01 QXU Discharge destination 4686 2025 3 2025-03-01 QRL Discharge destination 9374 2025 3 2025-03-01 QU9 Discharge destination 7 2025 3 2025-03-01 QKS Discharge destination 67 2025 3 2025-03-01 QR1 Discharge destination 1881 2025 3 2025-03-01 QT1 Discharge destination 253 2025 3 2025-03-01 QVV Discharge destination 4059 2025 3 2025-03-01 QU9 Discharge destination 6379 2025 3 2025-03-01 QE1 Discharge destination 75 2025 3 2025-03-01 QSL Discharge destination 118 2025 3 2025-03-01 QRL Discharge destination 260 2025 3 2025-03-01 QNC Discharge destination 0 2025 3 2025-03-01 QKK Discharge destination 5 2025 3 2025-03-01 QNX Discharge destination 96 2025 3 2025-03-01 QOQ Discharge destination 103 2025 3 2025-03-01 QVV Discharge destination 177 2025 3 2025-03-01 QHL Discharge destination 220 2025 3 2025-03-01 QOC Discharge destination 237 2025 3 2025-03-01 QMM Discharge destination 33 2025 3 2025-03-01 QU9 Discharge destination 390 2025 3 2025-03-01 QT6 Discharge destination 38 2025 3 2025-03-01 QT1 Discharge destination 121 2025 3 2025-03-01 QR1 Discharge destination 0 2025 3 2025-03-01 QUA Discharge destination 96 2025 3 2025-03-01 QE1 Discharge destination 275 2025 3 2025-03-01 QOX Discharge destination 0 2025 3 2025-03-01 QOC Discharge destination 207 2025 3 2025-03-01 QUY Discharge destination 49 2025 3 2025-03-01 QWE Discharge destination 79 2025 3 2025-03-01 QH8 Discharge destination 225 2025 3 2025-03-01 QUE Discharge destination 36 2025 3 2025-03-01 QOQ Discharge destination 27 2025 3 2025-03-01 QT1 Discharge destination 657 2025 3 2025-03-01 QHL Discharge destination 0 2025 3 2025-03-01 QWE Discharge destination 25 2025 3 2025-03-01 QPM Discharge destination 121 2025 3 2025-03-01 QH8 Discharge destination 3 2025 3 2025-03-01 QYG Discharge destination 7 2025 3 2025-03-01 QUA Discharge destination 99 2025 3 2025-03-01 QRV Discharge destination 7886 2025 3 2025-03-01 QRL Discharge destination 135 2025 3 2025-03-01 QYG Discharge destination 505 2025 3 2025-03-01 QMJ Discharge destination 191 2025 3 2025-03-01 QK1 Discharge destination 7395 2025 

In [0]:
from pyspark.sql import functions as F

silver = spark.table("databricks_cata.silver.acute_discharge_situation")

dest = (
    silver
    .filter("level = 'ICB' AND metric_group = 'Discharge destination'")
    .select(
        F.to_date(F.col("period"), "yyyy-MM-dd").alias("date_key"),
        F.col("org_code"),
        F.col("value"),
        F.col("year"),
        F.col("month"),
        F.when(F.col("metric").startswith("Pathway 0:"), F.lit("P0"))
         .when(F.col("metric").startswith("Pathway 1:"), F.lit("P1"))
         .when(F.col("metric").startswith("Pathway 2:"), F.lit("P2"))
         .when(F.col("metric").startswith("Pathway 3:"), F.lit("P3"))
         .otherwise(F.lit(None))
         .alias("pathway_code")
    )
    .filter(F.col("pathway_code").isNotNull())
)

fact_discharge_dest = (
    dest
    .groupBy("date_key", "org_code", "year", "month")
    .pivot("pathway_code", ["P0", "P1", "P2", "P3"])
    .agg(F.expr("sum(value)"))
    .na.fill(0)
)

fact_discharge_dest.write \
    .mode("overwrite") \
    .format("delta") \
    .partitionBy("year", "month") \
    .saveAsTable("databricks_cata.gold.fact_discharge_destination")

In [0]:
%sql
select * from databricks_cata.gold.fact_discharge_destination

date_key org_code year month P0 P1 P2 P3 2025-04-01 QOC 2025 4 2208 232 224 58 2025-04-01 QMM 2025 4 4840 755 340 106 2025-04-01 QNX 2025 4 5678 535 266 104 2025-04-01 QT1 2025 4 6358 859 156 99 2025-04-01 QKS 2025 4 5931 602 361 169 2025-04-01 QHG 2025 4 4422 537 165 69 2025-04-01 QM7 2025 4 5487 494 221 109 2025-04-01 QJM 2025 4 1968 269 37 77 2025-04-01 QVV 2025 4 4367 361 152 44 2025-04-01 QYG 2025 4 12461 1659 467 354 2025-04-01 QK1 2025 4 7200 448 292 47 2025-04-01 QRL 2025 4 9514 1106 476 175 2025-04-01 QKK 2025 4 8584 635 117 92 2025-04-01 QMF 2025 4 7562 686 107 134 2025-04-01 QHL 2025 4 2218 510 265 10 2025-04-01 QF7 2025 4 9654 787 253 105 2025-04-01 QGH 2025 4 3665 466 52 80 2025-04-01 QOP 2025 4 11244 1549 451 214 2025-04-01 QUA 2025 4 5494 869 193 276 2025-04-01 QJK 2025 4 8392 764 425 150 2025-04-01 QOX 2025 4 4157 525 137 54 2025-04-01 QUE 2025 4 5400 675 128 166 2025-04-01 QR1 2025 4 2000 205 131 0 2025-04-01 QWE 2025 4 3892 563 66 87 2025-04-01 QMJ 2025 4 6320 824 214 94 2025-04-01 QWO 2025 4 12663 1226 322 176 2025-04-01 QWU 2025 4 3119 599 169 64 2025-04-01 QNQ 2025 4 3197 588 51 44 2025-04-01 QH8 2025 4 5722 858 377 21 2025-04-01 QOQ 2025 4 6241 506 387 134 2025-04-01 QU9 2025 4 5595 424 180 69 2025-04-01 QSL 2025 4 2824 235 96 77 2025-04-01 QHM 2025 4 15047 2100 543 288 2025-04-01 QNC 2025 4 3113 1002 164 256 2025-04-01 QUY 2025 4 5540 754 166 147 2025-04-01 QXU 2025 4 4694 293 126 110 2025-04-01 QE1 2025 4 8032 777 238 180 2025-04-01 QT6 2025 4 1828 301 165 33 2025-04-01 QJG 2025 4 6039 373 237 65 2025-04-01 QPM 2025 4 3360 280 113 99 2025-04-01 QRV 2025 4 7912 1716 277 150 2025-04-01 QJ2 2025 4 6140 585 253 83 2024-07-01 QGH 2024 7 4996 388 77 88 2024-07-01 QOQ 2024 7 11188 433 309 100 2024-07-01 QUY 2024 7 6036 733 161 157 2024-07-01 QJM 2024 7 411 377 47 86 2024-07-01 QKS 2024 7 5641 496 310 188 2024-07-01 QOC 2024 7 2451 193 201 73 2024-07-01 QNQ 2024 7 3476 580 69 39 2024-07-01 QWU 2024 7 1872 560 77 103 2024-07-01 QUA 2024 7 5484 850 198 277 2024-07-01 QJK 2024 7 9930 643 345 102 2024-07-01 QWE 2024 7 6478 551 151 126 2024-07-01 QMJ 2024 7 7262 833 181 50 2024-07-01 QNX 2024 7 6773 478 301 133 2024-07-01 QM7 2024 7 5600 650 301 60 2024-07-01 QNC 2024 7 3637 1017 186 328 2024-07-01 QOP 2024 7 11492 1528 387 284 2024-07-01 QF7 2024 7 11243 688 214 202 2024-07-01 QJG 2024 7 6294 411 247 71 2024-07-01 QVV 2024 7 4373 417 108 62 2024-07-01 QHG 2024 7 4509 503 187 73 2024-07-01 QR1 2024 7 2230 155 150 0 2024-07-01 QWO 2024 7 13641 1258 224 199 2024-07-01 QT1 2024 7 5150 2689 155 45 2024-07-01 QJ2 2024 7 7791 434 250 67 2024-07-01 QHL 2024 7 1355 309 271 17 2024-07-01 QMM 2024 7 6055 766 295 115 2024-07-01 QK1 2024 7 7278 458 335 78 2024-07-01 QMF 2024 7 7541 692 135 154 2024-07-01 QH8 2024 7 6649 966 282 95 2024-07-01 QXU 2024 7 3936 301 120 106 2024-07-01 QHM 2024 7 15656 1496 502 345 2024-07-01 QE1 2024 7 9055 685 334 113 2024-07-01 QU9 2024 7 8602 587 147 92 2024-07-01 QRL 2024 7 7690 988 295 111 2024-07-01 QSL 2024 7 2943 217 137 59 2024-07-01 QPM 2024 7 3482 291 77 89 2024-07-01 QKK 2024 7 8538 660 159 120 2024-07-01 QUE 2024 7 5733 497 158 115 2024-07-01 QYG 2024 7 11691 1691 537 436 2024-07-01 QT6 2024 7 2070 275 179 33 2024-07-01 QOX 2024 7 0 0 0 0 2024-07-01 QRV 2024 7 9650 1610 310 181 2025-01-01 QMJ 2025 1 6362 785 142 107 2025-01-01 QGH 2025 1 3737 458 63 105 2025-01-01 QT1 2025 1 6540 982 200 111 2025-01-01 QJG 2025 1 5885 395 288 58 2025-01-01 QHM 2025 1 14984 1803 550 325 2025-01-01 QE1 2025 1 8255 775 263 190 2025-01-01 QJM 2025 1 2125 366 59 71 2025-01-01 QK1 2025 1 7381 495 343 59 2025-01-01 QOX 2025 1 4830 711 174 76 2025-01-01 QJ2 2025 1 6459 706 373 115 2025-01-01 QR1 2025 1 1810 220 165 0 2025-01-01 QT6 2025 1 1843 368 150 48 2025-01-01 QSL 2025 1 2737 304 131 77 2025-01-01 QF7 2025 1 10088 792 225 127 2025-01-01 QOC 2025 1 2150 241 241 71 2025-01-01 QU9 2025 1 7077 458 196 79 2025-01-01 QWE 2025 1 3654 535 78 103 2025-01-01 QRV 2025 1 7871 1901 310 184 2025-01-01 QM7 2025 1 4706 61

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import trim, col, when, lit

spark = SparkSession.builder.getOrCreate()

# 1a) Grab every unique free-text reason
unique_reasons = (
    spark.table("databricks_cata.silver.acute_discharge_situation")
         .filter("metric_group = 'Delay reason'")
         .select(trim(col("metric")).alias("metric_text"))
         .distinct()
)

In [0]:
from pyspark.sql.functions import when, lit, trim, col

# 2) Hard-code the mapping above
dim_delay_reason = unique_reasons.withColumn(
    "reason_code",
    when(col("metric_text") == "Wellbeing concerns � Awaiting determination of mental capacity",               lit("B3"))
   .when(col("metric_text") == "Capacity � Other home-based social care service not yet available (Pathway 1)", lit("E"))
   .when(col("metric_text") == "Interface�process � Patient/family/carer choice discussions on package still underway", lit("C"))
   .when(col("metric_text") == "Interface�process � End of life care inc Fast-Track CHC arrangement still underway?(Pathway 1 or 3)", lit("C"))
   .when(col("metric_text") == "Capacity � Housing adaptations not yet completed (Pathway 1 or 3)",             lit("E"))
   .when(col("metric_text") == "Capacity � Housing provision not yet available (Pathway 0 or 1)",              lit("E"))
   .when(col("metric_text") == "Capacity � Home-based rehabilitation, reablement or recovery services not yet available�(Pathway 1)", lit("E"))
   .when(col("metric_text") == "Capacity � Equipment and associated training not yet delivered (Pathway 1-3)", lit("E"))
   .when(col("metric_text") == "Hospital process - Awaiting medical review of need for supported discharge",     lit("A1"))
   .when(col("metric_text") == "Interface process � Residential/nursing home care arrangements still underway (Pathway 3)", lit("C"))
   .when(col("metric_text") == "Capacity � Other home-based community health services not yet available (Pathway 1)", lit("E"))
   .when(col("metric_text") == "Capacity � Residential/nursing home care not yet available (Pathway 3)",       lit("E"))
   .when(col("metric_text") == "Wellbeing concerns � Patient�/family/carer concerns over discharge readiness",  lit("B2"))
   .when(col("metric_text") == "Interface�process � Self-funded care package arrangements still underway",      lit("C"))
   .when(col("metric_text") == "Hospital process � Awaiting therapy review of need for supported discharge",     lit("A7"))
   .when(col("metric_text") == "Hospital process � Awaiting medicines to take home, discharge letter�or other discharge documentation", lit("A5"))
   .when(col("metric_text") == "Hospital process � Awaiting referral to care transfer hub for supported discharge", lit("C"))
   .when(col("metric_text") == "Care transfer hub process� Awaiting necessary referrals by care transfer hub",   lit("C"))
   .when(col("metric_text") == "Hospital process � Remaining in hospital due to infection prevention and control restrictions", lit("B4"))
   .when(col("metric_text") == "Wellbeing concerns � Ongoing�safeguarding concern",                            lit("B3"))
   .when(col("metric_text") == "Interface�process � Out of area discharge arrangements requested but not completed", lit("C"))
   .when(col("metric_text") == "Capacity � Bed-based rehabilitation, reablement or recovery services not yet available (Pathway 2)", lit("E"))
   .when(col("metric_text") == "Hospital process � Awaiting formal decision to discharge (inc diagnostic test results)", lit("A1"))
   .when(col("metric_text") == "Care transfer hub process � Waiting for confirmation of immediate care needs and pathway", lit("C"))
   .when(col("metric_text") == "Hospital process � Awaiting patient transport services",                      lit("A8"))
   .when(col("metric_text") == "Capacity � End of life care inc Fast-Track CHC not yet available�(Pathway 1 or 3)", lit("E"))
   .when(col("metric_text") == "Capacity � Awaiting restart of existing social care arrangements (Pathway 0)", lit("E"))
   .when(col("metric_text") == "Capacity � Mental health admitted patient care not yet available (Pathway 2)", lit("E"))
   .when(col("metric_text") == "Interface�process � Further action requested by agreed provider",            lit("C"))
   .when(col("metric_text") == "Care transfer hub process � Awaiting confirmation of funding eligibility",     lit("C"))
   .when(col("metric_text") == "Interface process � Home based rehabilitation, reablement or recovery service arrangements still underway (Pathway 1)", lit("C"))
   .when(col("metric_text") == "Interface process � Bed-based rehabilitation, reablement or recovery service arrangements still underway (Pathway 2)", lit("C"))
   .when(col("metric_text") == "Interface�process � Housing provision arrangement for homelessness still underway�(Pathway 0 or 1)", lit("C"))
   .when(col("metric_text") == "Interface process � Other home-based social care service arrangements still underway (Pathway 1)", lit("C"))
   .when(col("metric_text") == "Interface�process � Homeless with no recourse to public funds?",         lit("B1"))
   .when(col("metric_text") == "Wellbeing concerns - Issues with discharge destination readiness",         lit("B2"))
   .when(col("metric_text") == "Interface process � Other home-based community health service arrangements still underway (Pathway 1)", lit("C"))
   .otherwise(lit("UNKNOWN"))
)

In [0]:
dim_delay_reason.write.format("delta").mode("overwrite").saveAsTable("databricks_cata.gold.dim_delay_reason")

In [0]:
%sql
select * from databricks_cata.gold.dim_delay_reason

metric_text reason_code Wellbeing concerns � Awaiting determination of mental capacity B3 Capacity � Other home-based social care service not yet available (Pathway 1) E Interface�process � Patient/family/carer choice discussions on package still underway C Interface�process � End of life care inc Fast-Track CHC arrangement still underway?(Pathway 1 or 3) C Capacity � Housing adaptations not yet completed (Pathway 1 or 3) E Capacity � Housing provision not yet available (Pathway 0 or 1) E Capacity � Home-based rehabilitation, reablement or recovery services not yet available�(Pathway 1) E Capacity � Equipment and associated training not yet delivered (Pathway 1-3) E Hospital process - Awaiting medical review of need for supported discharge A1 Interface process � Residential/nursing home care arrangements still underway (Pathway 3) C Capacity � Other home-based community health services not yet available (Pathway 1) E Capacity � Residential/nursing home care not yet available (Pathway 3) E Wellbeing concerns � Patient�/family/carer concerns over discharge readiness B2 Interface�process � Self-funded care package arrangements still underway C Hospital process � Awaiting therapy review of need for supported discharge A7 Hospital process � Awaiting medicines to take home, discharge letter�or other discharge documentation A5 Hospital process � Awaiting referral to care transfer hub for supported discharge C Care transfer hub process� Awaiting necessary referrals by care transfer hub C Hospital process � Remaining in hospital due to infection prevention and control restrictions B4 Wellbeing concerns � Ongoing�safeguarding concern B3 Interface�process � Out of area discharge arrangements requested but not completed C Capacity � Bed-based rehabilitation, reablement or recovery services not yet available (Pathway 2) E Hospital process � Awaiting formal decision to discharge (inc diagnostic test results) A1 Care transfer hub process � Waiting for confirmation of immediate care needs and pathway C Hospital process � Awaiting patient transport services A8 Capacity � End of life care inc Fast-Track CHC not yet available�(Pathway 1 or 3) E Capacity � Awaiting restart of existing social care arrangements (Pathway 0) E Capacity � Mental health admitted patient care not yet available (Pathway 2) E Interface�process � Further action requested by agreed provider C Care transfer hub process � Awaiting confirmation of funding eligibility C Interface process � Home based rehabilitation, reablement or recovery service arrangements still underway (Pathway 1) C Interface process � Bed-based rehabilitation, reablement or recovery service arrangements still underway (Pathway 2) C Interface�process � Housing provision arrangement for homelessness still underway�(Pathway 0 or 1) C Interface process � Other home-based social care service arrangements still underway (Pathway 1) C Interface�process � Homeless with no recourse to public funds? B1 Wellbeing concerns - Issues with discharge destination readiness B2 Interface process � Other home-based community health service arrangements still underway (Pathway 1) C

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import to_date, col, sum as Fsum, avg as Favg, stddev as Fstd
from pyspark.sql.window import Window

spark = SparkSession.builder.getOrCreate()

# 1) Read Silver delay-reason rows and add date_key
silver = (
    spark.table("databricks_cata.silver.acute_discharge_situation")
         .filter("metric_group = 'Delay reason'")
         .select(
             to_date("period", "yyyy-MM-dd").alias("date_key"),
             col("org_code"),
             col("metric"),
             col("value").alias("delay_count"),
             col("year"),
             col("month")
         )
)

# 2) Join to Dim-Delay-Reason (which has metric_text→reason_code)
dim_delay = spark.table("databricks_cata.gold.dim_delay_reason")

fact_delay_reason = (
    silver
      .join(dim_delay,
            silver.metric == dim_delay.metric_text,
            how="inner")
      .select(
         "date_key",
         col("org_code").alias("icb_code"),
         col("reason_code"),
         "delay_count",
         "year","month"
      )
)



In [0]:
# Persist the fact table
(
  fact_delay_reason
    .write
    .mode("overwrite")
    .format("delta")
    .saveAsTable("databricks_cata.gold.fact_delay_reason")
)



In [0]:
%sql
select * from databricks_cata.gold.fact_delay_reason

date_key icb_code reason_code delay_count year month 2025-04-01 R0A C 34 2025 4 2025-04-01 RCD A8 0 2025 4 2025-04-01 RWA A5 0 2025 4 2025-04-01 RN5 B4 0 2025 4 2025-04-01 QMF B2 4 2025 4 2025-04-01 RTR B3 0 2025 4 2025-04-01 QU9 B2 1 2025 4 2025-04-01 RTX C 0 2025 4 2025-04-01 QMM C 0 2025 4 2025-04-01 RVW C 0 2025 4 2025-04-01 RN3 C 1 2025 4 2025-04-01 RWP C 2 2025 4 2025-04-01 RJ2 C 2 2025 4 2025-04-01 QT6 B1 0 2025 4 2025-04-01 RJN B1 0 2025 4 2025-04-01 QOC C 0 2025 4 2025-04-01 RJZ C 6 2025 4 2025-04-01 QNX C 1 2025 4 2025-04-01 RYR E 0 2025 4 2025-04-01 QU9 E 1 2025 4 2025-04-01 RDE E 0 2025 4 2025-04-01 RKE E 0 2025 4 2025-04-01 RBL E 3 2025 4 2025-04-01 Y61 E 22 2025 4 2025-04-01 QUA E 1 2025 4 2025-04-01 R1H E 0 2025 4 2024-09-01 QR1 A7 2 2024 9 2024-09-01 RWD A1 29 2024 9 2024-09-01 RCD A1 0 2024 9 2024-09-01 REM B4 0 2024 9 2024-09-01 QUE A1 24 2024 9 2024-09-01 RAE A1 2 2024 9 2024-09-01 RX1 B2 0 2024 9 2024-09-01 RF4 B3 1 2024 9 2024-09-01 RBL C 12 2024 9 2024-09-01 RA9 C 1 2024 9 2024-09-01 QWE C 6 2024 9 2024-09-01 RQW C 0 2024 9 2024-09-01 Y62 C 9 2024 9 2024-09-01 RTK C 10 2024 9 2024-09-01 QRV C 2 2024 9 2024-09-01 RKB C 1 2024 9 2024-09-01 R0A C 1 2024 9 2024-09-01 RJL C 0 2024 9 2024-09-01 RN5 C 0 2024 9 2024-09-01 RAJ C 1 2024 9 2024-09-01 QK1 C 3 2024 9 2024-09-01 RXC C 1 2024 9 2024-09-01 RA7 E 9 2024 9 2024-09-01 Y60 E 30 2024 9 2024-09-01 RXK E 0 2024 9 2024-09-01 RWG E 0 2024 9 2024-09-01 RA9 E 1 2024 9 2024-09-01 RVR E 0 2024 9 2024-09-01 RX1 E 8 2024 9 2024-09-01 QT6 E 0 2024 9 2024-09-01 REF E 0 2024 9 2024-09-01 RJ1 E 0 2024 9 2024-07-01 QT6 A5 0 2024 7 2024-07-01 Y56 B4 1 2024 7 2024-07-01 RWJ B4 0 2024 7 2024-07-01 QJK A1 19 2024 7 2024-07-01 RXW B2 0 2024 7 2024-07-01 RGT B3 0 2024 7 2024-07-01 RYJ B3 0 2024 7 2024-07-01 RWD C 1 2024 7 2024-07-01 RFR C 0 2024 7 2024-07-01 QH8 C 2 2024 7 2024-07-01 RVV C 0 2024 7 2024-07-01 QNC C 0 2024 7 2024-07-01 RQM C 1 2024 7 2024-07-01 RTP C 10 2024 7 2024-07-01 RCD E 0 2024 7 2024-07-01 RAE E 0 2024 7 2024-07-01 RXP E 0 2024 7 2024-07-01 RBT E 15 2024 7 2024-07-01 RHU E 9 2024 7 2024-07-01 RNQ E 5 2024 7 2024-07-01 RVV E 9 2024 7 2024-07-01 RBD E 2 2024 7 2024-07-01 RCF E 0 2024 7 2025-01-01 RA7 A7 0 2025 1 2025-01-01 RXL A1 0 2025 1 2025-01-01 RA9 A1 0 2025 1 2025-01-01 ENG A8 108 2025 1 2025-01-01 ENG A5 164 2025 1 2025-01-01 QUY A5 0 2025 1 2025-01-01 RAJ B4 0 2025 1 2025-01-01 RX1 B3 0 2025 1 2025-01-01 QRV B2 10 2025 1 2025-01-01 RMC B2 2 2025 1 2025-01-01 RTX B2 0 2025 1 2025-01-01 RGN C 0 2025 1 2025-01-01 RXP C 0 2025 1 2025-01-01 RMC C 1 2025 1 2025-01-01 QRL C 22 2025 1 2025-01-01 RFF C 0 2025 1 2025-01-01 RTP C 4 2025 1 2025-01-01 RP5 C 0 2025 1 2025-01-01 RGN C 0 2025 1 2025-01-01 RVR C 4 2025 1 2025-01-01 RD8 C 4 2025 1 2025-01-01 RAS C 1 2025 1 2025-01-01 RWD C 4 2025 1 2025-01-01 RN5 C 5 2025 1 2025-01-01 QWE C 1 2025 1 2025-01-01 RH5 C 3 2025 1 2025-01-01 RQX C 0 2025 1 2025-01-01 REF C 0 2025 1 2025-01-01 QU9 C 1 2025 1 2025-01-01 QNQ C 0 2025 1 2025-01-01 RJ2 C 0 2025 1 2025-01-01 RRK E 5 2025 1 2025-01-01 Y60 E 3 2025 1 2025-01-01 RKE E 0 2025 1 2025-01-01 REM E 0 2025 1 2025-01-01 QK1 E 0 2025 1 2025-01-01 Y63 E 74 2025 1 2025-01-01 RRV E 0 2025 1 2025-01-01 RAS E 0 2025 1 2025-01-01 Y63 E 80 2025 1 2025-01-01 RNA E 0 2025 1 2025-01-01 Y60 E 14 2025 1 2025-04-01 R0B A7 2 2025 4 2025-04-01 RJC C 0 2025 4 2025-04-01 QJG B2 1 2025 4 2025-04-01 RA7 B2 0 2025 4 2025-04-01 RDU B2 0 2025 4 2025-04-01 RWY C 1 2025 4 2025-04-01 RN3 C 1 2025 4 2025-04-01 RWG C 0 2025 4 2025-04-01 RN5 C 5 2025 4 2025-04-01 RN7 C 0 2025 4 2025-04-01 RH8 C 0 2025 4 2025-04-01 Y58 C 49 2025 4 2025-04-01 QKK C 2 2025 4 2025-04-01 RNA C 0 2025 4 2025-04-01 QF7 B1 1 2025 4 2025-04-01 QWO C 0 2025 4 2025-04-01 RJ1 C 1 2025 4 2025-04-01 RJE C 3 2025 4 2025-04-01 RM1 E 4 2025 4 2025-04-01 RDU E 6 2025 4 2025-04-01 RQX E 0 2025 4 2025-04-01 RAL E 5 2025 4 2025-04-01 RTP E 1 2025 4 2025-04-01 RDU E 0 2025 4 2025-04-01 RNZ E 0 2025 4 2024-09-01 Y60 A1 50 2024 9 2024-09-01 Q

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

# --- assume fact_delay_reason is already defined as:
# fact_delay_reason = spark.table("databricks_cata.gold.fact_delay_reason")

# 3a) Compute peer averages & stddev per reason × month
peer_stats = (
    fact_delay_reason
      .groupBy("reason_code","year","month")
      .agg(
        F.avg("delay_count").alias("peer_avg"),
        F.stddev("delay_count").alias("peer_std")
      )
)

# 3b) Join back & calculate z-score
barrier_zscores = (
    fact_delay_reason.alias("f")
      .join(peer_stats.alias("p"),
            on=[
              F.col("f.reason_code") == F.col("p.reason_code"),
              F.col("f.year")        == F.col("p.year"),
              F.col("f.month")       == F.col("p.month")
            ],
            how="inner"
      )
      .select(
        F.col("f.icb_code"),
        F.col("f.reason_code").alias("barrier"),
        F.col("f.year"),
        F.col("f.month"),
        F.col("f.delay_count").alias("total_barrier"),
        F.col("p.peer_avg"),
        (
          (F.col("f.delay_count") - F.col("p.peer_avg")) 
          / F.col("p.peer_std")
        ).alias("z_score_barrier")
      )
)

# **Write out as a Delta table**
barrier_zscores.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("databricks_cata.gold.fact_barrier_zscores")


# 4) Rank & pick Top-3 per ICB × month
window_spec = Window.partitionBy("icb_code","year","month") \
                    .orderBy(F.desc("total_barrier"))

top3 = (
    barrier_zscores
      .withColumn("rank", F.rank().over(window_spec))
      .filter("rank <= 3")
      .select("icb_code","year","month","barrier","total_barrier","rank")
)

# **Write out as a Delta table**
top3.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("databricks_cata.gold.fact_top3_delay_reasons")


In [0]:
%sql
select * from databricks_cata.gold.fact_barrier_zscores

icb_code barrier year month total_barrier peer_avg z_score_barrier R0A C 2025 4 34 6.14920634920635 0.9602052089717122 RCD A8 2025 4 0 2.6785714285714284 -0.2777759980895458 RWA A5 2025 4 0 4.303571428571429 -0.2819199723295389 RN5 B4 2025 4 0 0.75 -0.25616737782707866 QMF B2 2025 4 4 2.738095238095238 0.12474118775887923 RTR B3 2025 4 0 2.7916666666666665 -0.2690546408726303 QU9 B2 2025 4 1 2.738095238095238 -0.1718133340829846 RTX C 2025 4 0 6.14920634920635 -0.2120047292577461 QMM C 2025 4 0 6.14920634920635 -0.2120047292577461 RVW C 2025 4 0 6.14920634920635 -0.2120047292577461 RN3 C 2025 4 1 6.14920634920635 -0.1775279663686444 RWP C 2025 4 2 6.14920634920635 -0.14305120347954267 RJ2 C 2025 4 2 6.14920634920635 -0.14305120347954267 QT6 B1 2025 4 0 0.6071428571428571 -0.2561717123738196 RJN B1 2025 4 0 0.6071428571428571 -0.2561717123738196 QOC C 2025 4 0 6.14920634920635 -0.2120047292577461 RJZ C 2025 4 6 6.14920634920635 -0.0051441519231358234 QNX C 2025 4 1 6.14920634920635 -0.1775279663686444 RYR E 2025 4 0 6.378787878787879 -0.1965716420067634 QU9 E 2025 4 1 6.378787878787879 -0.16575518506508552 RDE E 2025 4 0 6.378787878787879 -0.1965716420067634 RKE E 2025 4 0 6.378787878787879 -0.1965716420067634 RBL E 2025 4 3 6.378787878787879 -0.10412227118172977 Y61 E 2025 4 22 6.378787878787879 0.4813904107101497 QUA E 2025 4 1 6.378787878787879 -0.16575518506508552 R1H E 2025 4 0 6.378787878787879 -0.1965716420067634 QR1 A7 2024 9 2 9.285714285714286 -0.24370151966528303 RWD A1 2024 9 29 6.383928571428571 1.0259442078400338 RCD A1 2024 9 0 6.383928571428571 -0.2895973583125243 REM B4 2024 9 0 0.4880952380952381 -0.27986019205527135 QUE A1 2024 9 24 6.383928571428571 0.7991266964344204 RAE A1 2024 9 2 6.383928571428571 -0.19887035375027892 RX1 B2 2024 9 0 2.2886904761904763 -0.30214924278170513 RF4 B3 2024 9 1 2.3154761904761907 -0.17322797367634213 RBL C 2024 9 12 5.589682539682539 0.2625796560610603 RA9 C 2024 9 1 5.589682539682539 -0.1880027424787807 QWE C 2024 9 6 5.589682539682539 0.016807438675692496 RQW C 2024 9 0 5.589682539682539 -0.22896477870967535 Y62 C 2024 9 9 5.589682539682539 0.13969354736837641 RTK C 2024 9 10 5.589682539682539 0.18065558359927106 QRV C 2024 9 2 5.589682539682539 -0.14704070624788607 RKB C 2024 9 1 5.589682539682539 -0.1880027424787807 R0A C 2024 9 1 5.589682539682539 -0.1880027424787807 RJL C 2024 9 0 5.589682539682539 -0.22896477870967535 RN5 C 2024 9 0 5.589682539682539 -0.22896477870967535 RAJ C 2024 9 1 5.589682539682539 -0.1880027424787807 QK1 C 2024 9 3 5.589682539682539 -0.10607867001699142 RXC C 2024 9 1 5.589682539682539 -0.1880027424787807 RA7 E 2024 9 9 5.278679653679654 0.145042726994038 Y60 E 2024 9 30 5.278679653679654 0.9635418035077252 RXK E 2024 9 0 5.278679653679654 -0.20574259151182794 RWG E 2024 9 0 5.278679653679654 -0.20574259151182794 RA9 E 2024 9 1 5.278679653679654 -0.16676644501117618 RVR E 2024 9 0 5.278679653679654 -0.20574259151182794 RX1 E 2024 9 8 5.278679653679654 0.10606658049338623 QT6 E 2024 9 0 5.278679653679654 -0.20574259151182794 REF E 2024 9 0 5.278679653679654 -0.20574259151182794 RJ1 E 2024 9 0 5.278679653679654 -0.20574259151182794 QT6 A5 2024 7 0 2.970059880239521 -0.2825130349670338 Y56 B4 2024 7 1 0.8862275449101796 0.034561700952411074 RWJ B4 2024 7 0 0.8862275449101796 -0.2692174600503599 QJK A1 2024 7 19 6.949101796407185 0.49024400542234503 RXW B2 2024 7 0 2.3293413173652695 -0.29035292276602537 RGT B3 2024 7 0 2.3862275449101795 -0.28705463134557574 RYJ B3 2024 7 0 2.3862275449101795 -0.28705463134557574 RWD C 2024 7 1 5.815968063872256 -0.17664787605898805 RFR C 2024 7 0 5.815968063872256 -0.2133274955490216 QH8 C 2024 7 2 5.815968063872256 -0.13996825656895448 RVV C 2024 7 0 5.815968063872256 -0.2133274955490216 QNC C 2024 7 0 5.815968063872256 -0.2133274955490216 RQM C 2024 7 1 5.815968063872256 -0.17664787605898805 RTP C 2024 7 10 5.815968063872256 0.15346869935131413 RCD E 2024 7 0 6.707131192161132 -0.19317581742302722 RAE E 2024 7 0 6

In [0]:
%sql
select * from databricks_cata.gold.fact_top3_delay_reasons

icb_code year month barrier total_barrier rank ENG 2024 6 E 827 1 ENG 2024 6 E 804 2 ENG 2024 6 C 640 3 ENG 2024 7 E 891 1 ENG 2024 7 E 807 2 ENG 2024 7 C 645 3 ENG 2024 8 E 884 1 ENG 2024 8 E 814 2 ENG 2024 8 C 668 3 ENG 2024 9 E 677 1 ENG 2024 9 C 585 2 ENG 2024 9 E 572 3 ENG 2024 10 E 888 1 ENG 2024 10 C 753 2 ENG 2024 10 E 670 3 ENG 2024 11 E 864 1 ENG 2024 11 E 770 2 ENG 2024 11 C 699 3 ENG 2024 12 E 785 1 ENG 2024 12 E 745 2 ENG 2024 12 C 693 3 ENG 2025 1 E 962 1 ENG 2025 1 C 846 2 ENG 2025 1 E 735 3 ENG 2025 2 E 925 1 ENG 2025 2 C 827 2 ENG 2025 2 E 711 3 ENG 2025 3 E 966 1 ENG 2025 3 C 795 2 ENG 2025 3 E 762 3 ENG 2025 4 E 822 1 ENG 2025 4 C 736 2 ENG 2025 4 E 723 3 ENG 2025 5 E 835 1 ENG 2025 5 C 728 2 ENG 2025 5 E 698 3 QE1 2024 6 C 36 1 QE1 2024 6 C 29 2 QE1 2024 6 E 24 3 QE1 2024 7 C 39 1 QE1 2024 7 E 27 2 QE1 2024 7 C 18 3 QE1 2024 8 C 31 1 QE1 2024 8 E 21 2 QE1 2024 8 E 18 3 QE1 2024 9 C 30 1 QE1 2024 9 E 16 2 QE1 2024 9 E 14 3 QE1 2024 10 C 33 1 QE1 2024 10 C 18 2 QE1 2024 10 E 13 3 QE1 2024 11 C 44 1 QE1 2024 11 E 15 2 QE1 2024 11 C 13 3 QE1 2024 12 C 40 1 QE1 2024 12 A1 18 2 QE1 2024 12 E 16 3 QE1 2025 1 C 58 1 QE1 2025 1 E 22 2 QE1 2025 1 A1 18 3 QE1 2025 2 C 58 1 QE1 2025 2 E 24 2 QE1 2025 2 E 22 3 QE1 2025 3 C 56 1 QE1 2025 3 E 24 2 QE1 2025 3 C 23 3 QE1 2025 4 C 44 1 QE1 2025 4 E 21 2 QE1 2025 4 C 21 2 QE1 2025 5 C 39 1 QE1 2025 5 E 32 2 QE1 2025 5 C 21 3 QF7 2024 6 C 46 1 QF7 2024 6 E 35 2 QF7 2024 6 E 21 3 QF7 2024 7 C 70 1 QF7 2024 7 E 37 2 QF7 2024 7 E 22 3 QF7 2024 8 C 59 1 QF7 2024 8 E 48 2 QF7 2024 8 E 22 3 QF7 2024 9 C 52 1 QF7 2024 9 E 27 2 QF7 2024 9 E 21 3 QF7 2024 10 C 73 1 QF7 2024 10 E 34 2 QF7 2024 10 E 26 3 QF7 2024 11 C 79 1 QF7 2024 11 E 35 2 QF7 2024 11 E 24 3 QF7 2024 12 C 75 1 QF7 2024 12 E 38 2 QF7 2024 12 E 27 3 QF7 2025 1 C 102 1 QF7 2025 1 E 43 2 QF7 2025 1 E 33 3 QF7 2025 2 C 94 1 QF7 2025 2 E 33 2 QF7 2025 2 E 29 3 QF7 2025 3 C 83 1 QF7 2025 3 E 41 2 QF7 2025 3 E 36 3 QF7 2025 4 C 70 1 QF7 2025 4 E 31 2 QF7 2025 4 E 29 3 QF7 2025 5 C 65 1 QF7 2025 5 E 27 2 QF7 2025 5 E 25 3 QGH 2024 6 E 14 1 QGH 2024 6 E 13 2 QGH 2024 6 A1 6 3 QGH 2024 7 E 10 1 QGH 2024 7 A1 5 2 QGH 2024 7 C 5 2 QGH 2024 8 E 10 1 QGH 2024 8 E 8 2 QGH 2024 8 E 8 2 QGH 2024 9 E 13 1 QGH 2024 9 E 6 2 QGH 2024 9 E 6 2 QGH 2024 9 C 6 2 QGH 2024 10 E 10 1 QGH 2024 10 E 10 1 QGH 2024 10 E 9 3 QGH 2024 11 E 12 1 QGH 2024 11 C 7 2 QGH 2024 11 E 6 3 QGH 2024 12 E 6 1 QGH 2024 12 E 5 2 QGH 2024 12 A1 5 2 QGH 2025 1 E 15 1 QGH 2025 1 E 8 2 QGH 2025 1 E 8 2 QGH 2025 2 E 16 1 QGH 2025 2 E 11 2 QGH 2025 2 E 10 3 QGH 2025 2 A1 10 3 QGH 2025 3 E 15 1 QGH 2025 3 E 13 2 QGH 2025 3 E 13 2 QGH 2025 4 E 10 1 QGH 2025 4 E 7 2 QGH 2025 4 C 7 2 QGH 2025 5 E 12 1 QGH 2025 5 E 10 2 QGH 2025 5 C 8 3 QH8 2024 6 C 12 1 QH8 2024 6 E 12 1 QH8 2024 6 A7 11 3 QH8 2024 7 E 20 1 QH8 2024 7 E 14 2 QH8 2024 7 A7 11 3 QH8 2024 8 E 18 1 QH8 2024 8 E 10 2 QH8 2024 8 A7 8 3 QH8 2024 9 E 13 1 QH8 2024 9 E 12 2 QH8 2024 9 E 8 3 QH8 2024 9 C 8 3 QH8 2024 10 E 20 1 QH8 2024 10 E 13 2 QH8 2024 10 E 11 3 QH8 2024 11 E 18 1 QH8 2024 11 E 15 2 QH8 2024 11 E 14 3 QH8 2024 12 E 14 1 QH8 2024 12 E 10 2 QH8 2024 12 E 10 2 QH8 2025 1 E 13 1 QH8 2025 1 A7 12 2 QH8 2025 1 E 12 2 QH8 2025 1 E 12 2 QH8 2025 2 E 13 1 QH8 2025 2 A7 13 1 QH8 2025 2 E 11 3 QH8 2025 2 E 11 3 QH8 2025 3 E 14 1 QH8 2025 3 E 13 2 QH8 2025 3 E 12 3 QH8 2025 4 E 13 1 QH8 2025 4 E 10 2 QH8 2025 4 E 10 2 QH8 2025 5 E 14 1 QH8 2025 5 E 11 2 QH8 2025 5 E 11 2 QHG 2024 6 C 33 1 QHG 2024 6 E 19 2 QHG 2024 6 C 14 3 QHG 2024 7 C 34 1 QHG 2024 7 C 20 2 QHG 2024 7 E 19 3 QHG 2024 8 C 30 1 QHG 2024 8 E 25 2 QHG 2024 8 C 20 3 QHG 2024 9 C 24 1 QHG 2024 9 E 23 2 QHG 2024 9 C 10 3 QHG 2024 10 C 40 1 QHG 2024 10 C 19 2 QHG 2024 10 E 18 3 QHG 2024 11 C 20 1 QHG 2024 11 C 17 2 QHG 2024 11 E 15 3 QHG 2024 12 C 18 1 QHG 2024 12 E 17 2 QHG 2024 12 C 17 2 QHG 2025 1 C 27 1 QHG 2025 1 E 21 2 QHG 2025 1 C 20 3 QHG 2025 2 C 27 1 QHG 2025 2 E 26 2 QHG 2025 2 C 13 3 QHG 2025 3 C 23 1 QHG 2025 3 E 23 1 QHG 2025 3 C 16 3 QHG

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import to_date, col, when, lit

# 1. Read your silver table
silver_a = spark.table("databricks_cata.silver.acute_discharge_situation")

# 2. Filter down to just the Additional‐bed‐days rows for ICBs, and parse out sub‐groups
additional = (
    silver_a
      .filter("level = 'ICB' AND metric_group = 'Additional bed days lost'")
      .withColumn("date_key", to_date(col("period"), "yyyy-MM-dd"))
      .withColumn(
         "length_band",
         when(col("metric").rlike("7\\+? days"),  "bed_days_7_plus")
         .when(col("metric").rlike("14\\+? days"), "bed_days_14_plus")
         .when(col("metric").rlike("21\\+? days"), "bed_days_21_plus")
         .otherwise(lit("other"))
      )
)




In [0]:
# 3. Pivot to wide form
fact_additional_bed_days = (
    additional
      .groupBy("date_key","org_code")
      .pivot("length_band", ["bed_days_7_plus","bed_days_14_plus","bed_days_21_plus"])
      .agg(F.sum("value").alias("total_days_lost"))
      .withColumn("year",  F.year("date_key"))
      .withColumn("month", F.month("date_key"))
)



In [0]:
display(fact_additional_bed_days)

date_key org_code bed_days_7_plus bed_days_14_plus bed_days_21_plus year month 2024-04-08 QUE 2630 2229 1852 2024 4 2024-09-02 QUE 1678 1460 1164 2024 9 2025-01-20 QUE 1789 1531 1203 2025 1 2025-05-26 QOQ 1098 906 648 2025 5 2024-04-29 QHM 3336 3047 2567 2024 4 2024-07-15 QMF 1636 1561 1436 2024 7 2024-12-23 QOP 11087 10611 10010 2024 12 2025-01-13 QU9 1512 1315 1048 2025 1 2025-04-14 QYG 13255 12575 11415 2025 4 2025-02-10 QWE 3801 3615 3308 2025 2 2025-05-05 QE1 2252 1894 1477 2025 5 2025-02-24 QOC 383 305 250 2025 2 2024-04-22 QK1 1121 970 842 2024 4 2025-02-17 QWU 2075 1875 1548 2025 2 2024-04-15 QNQ 3896 3684 3350 2024 4 2024-09-23 QOP 11955 11535 10882 2024 9 2025-01-13 QJM 795 656 516 2025 1 2025-02-24 QT6 930 868 763 2025 2 2025-05-19 QNC 316 273 190 2025 5 2024-04-29 QU9 1264 1100 920 2024 4 2024-04-01 QT6 1421 1371 1286 2024 4 2024-11-25 QHL 1222 1065 986 2024 11 2024-07-01 QRL 4733 4413 3737 2024 7 2024-08-19 QXU 3236 3143 3009 2024 8 2025-03-03 QM7 390 320 257 2025 3 2024-09-23 QJG 1032 769 661 2024 9 2025-02-10 QNX 7939 7539 6819 2025 2 2024-09-30 QNX 10960 10728 10220 2024 9 2024-04-15 QU9 1493 1396 1194 2024 4 2024-05-27 QUA 1548 1431 1232 2024 5 2024-11-04 QMJ 3181 3016 2683 2024 11 2024-11-11 QHG 2304 2045 1787 2024 11 2025-04-21 QM7 377 333 231 2025 4 2024-09-02 QK1 1464 1248 1019 2024 9 2024-04-01 QKS 3882 3550 3115 2024 4 2024-05-06 QVV 3646 3561 3399 2024 5 2024-10-14 QNQ 3784 3621 3427 2024 10 2025-01-27 QT1 1324 1148 975 2025 1 2025-02-10 QOC 507 394 322 2025 2 2024-05-27 QWU 99 78 69 2024 5 2025-03-24 QXU 1602 1508 1381 2025 3 2024-06-24 QT6 1100 1060 990 2024 6 2024-11-11 QF7 3265 2786 2364 2024 11 2024-12-09 QR1 1263 1157 1048 2024 12 2024-06-03 QMJ 5045 4741 4370 2024 6 2024-05-27 QJK 1118 938 824 2024 5 2025-05-05 QWO 8376 7971 7375 2025 5 2024-09-02 QJG 805 717 620 2024 9 2025-05-05 QJM 858 726 593 2025 5 2025-05-19 QNX 8524 8056 7317 2025 5 2024-08-05 QNX 10478 10221 9747 2024 8 2025-04-07 QE1 2269 2009 1724 2025 4 2025-04-14 QR1 1124 1024 863 2025 4 2024-04-29 QJM 783 689 613 2024 4 2024-05-20 QJM 674 585 469 2024 5 2024-09-16 QUY 4145 3707 3203 2024 9 2025-02-17 QJK 1109 843 639 2025 2 2024-10-14 QMJ 4240 3817 3403 2024 10 2024-12-16 QJG 725 586 439 2024 12 2024-04-08 QUY 3898 3526 3125 2024 4 2025-05-26 QJM 753 679 599 2025 5 2024-12-30 QWO 7902 7432 6832 2024 12 2024-08-12 QKK 3902 3785 3555 2024 8 2025-03-31 QUY 4998 4542 4014 2025 3 2025-01-20 QKS 3562 3211 2548 2025 1 2024-05-06 QYG 13486 12981 12174 2024 5 2024-05-27 QOC 511 373 268 2024 5 2025-03-17 QRV 4354 4194 3963 2025 3 2024-07-01 QWE 2968 2863 2670 2024 7 2024-10-14 QE1 1418 1136 875 2024 10 2024-07-08 QNC 72 60 42 2024 7 2024-08-26 QU9 1160 1084 904 2024 8 2025-02-10 QXU 1950 1871 1710 2025 2 2025-02-24 QOQ 1405 1199 958 2025 2 2025-03-24 QMJ 3946 3777 3396 2025 3 2024-04-22 QH8 720 387 250 2024 4 2025-01-27 QJK 1136 919 707 2025 1 2024-07-22 QRV 4306 4069 3676 2024 7 2024-05-27 QMM 4677 4470 4068 2024 5 2025-03-17 QUY 4437 4107 3398 2025 3 2024-12-09 QKK 3813 3700 3502 2024 12 2025-03-24 QMF 3235 3117 2762 2025 3 2025-04-07 QWO 8452 8087 6177 2025 4 2024-10-14 QUA 1418 1215 960 2024 10 2025-03-17 QUE 1686 1445 1124 2025 3 2024-06-17 QKS 3498 3314 2851 2024 6 2024-06-17 QT6 1248 1207 1152 2024 6 2025-01-27 QJG 679 475 354 2025 1 2025-03-24 QT1 1096 958 788 2025 3 2025-01-13 QUE 1499 1297 976 2025 1 2025-04-28 QE1 2231 1940 1645 2025 4 2025-04-21 QNC 242 214 152 2025 4 2025-04-07 QVV 3926 3757 3484 2025 4 2025-03-17 QSL 1696 1539 1255 2025 3 2025-03-10 QWE 4440 4300 3966 2025 3 2025-05-05 QWE 3969 3855 3574 2025 5 2024-07-15 QJ2 870 646 473 2024 7 2024-07-22 QJM 677 600 494 2024 7 2024-12-23 QOQ 1394 1184 903 2024 12 2024-04-15 QSL 2191 2087 1929 2024 4 2024-07-22 QOX 0 0 0 2024 7 2024-09-09 QUE 1659 1422 1116 2024 9 2025-05-26 QRV 4281 4124 3806 2025 5 2025-02-03 QOQ 1577 1296 929 2025 2 2024-06-17 QKK 3446 3306 3087 2024 6 2025-04-28 QOQ 1126 964 683 2025 4 2024-12-16 QOQ 1259 996 760 2024 12 2024-06-03 QM7 628 505 436 2024 6 2025

In [0]:
# 4. Persist as a Delta table in your gold layer
fact_additional_bed_days.write\
    .mode("overwrite")\
    .format("delta")\
    .partitionBy("year","month")\
    .saveAsTable("databricks_cata.gold.fact_additional_bed_days")

In [0]:
from pyspark.sql import SparkSession, functions as F
from pyspark.sql.window import Window

spark = SparkSession.builder.getOrCreate()

# read your pivoted bed-days fact
fact_bed = spark.table("databricks_cata.gold.fact_additional_bed_days")

# 1) Unpivot to long form
fact_bed_long = fact_bed.selectExpr(
  "org_code as icb_code",
  "year", "month", "date_key",
  # stack(#cols, 'colName1', expr1, 'colName2', expr2, ...) → (length_band, total_days_lost)
  """
  stack(
    3,
    'bed_days_7_plus',   bed_days_7_plus,
    'bed_days_14_plus',  bed_days_14_plus,
    'bed_days_21_plus',  bed_days_21_plus
  ) as (length_band, total_days_lost)
  """
)

# 2) Compute peer means & stddev by bucket × year × month
peer_stats_bed = (
  fact_bed_long
    .groupBy("length_band","year","month")
    .agg(
      F.avg("total_days_lost").alias("peer_avg_days"),
      F.stddev("total_days_lost").alias("peer_std_days")
    )
)

# 3) Join back & compute Z-score
bed_zscores = (
  fact_bed_long.alias("f")
    .join(peer_stats_bed.alias("p"),
          on=["length_band","year","month"], how="inner")
    .select(
      F.col("f.icb_code"),
      F.col("f.date_key"),
      F.col("f.year"),
      F.col("f.month"),
      F.col("f.length_band"),
      F.col("f.total_days_lost"),
      F.col("p.peer_avg_days"),
      F.col("p.peer_std_days"),
      (
        (F.col("f.total_days_lost") - F.col("p.peer_avg_days"))
        / F.col("p.peer_std_days")
      ).alias("z_score_bed_days")
    )
)

# 4) Persist as a Delta table for Power BI consumption
bed_zscores.write \
  .format("delta") \
  .mode("overwrite") \
  .saveAsTable("databricks_cata.gold.fact_bed_days_zscores")
